In [1]:
import numpy as np
import pandas as pd
from matplotlib import pyplot as plt
import tifffile as tf
from scipy.ndimage.filters import gaussian_filter1d as gaussian
from glob import glob
from scipy.signal import savgol_filter, medfilt
from math import floor
import matplotlib.ticker as ticker
from scipy.optimize import curve_fit
# from plot_params import set_plot_params


In [2]:
# 1. load data into pandas data frame

# 2. convert data from I(t) to c_i(t) via equation for G quadruplex binding
    # - find t0
    # - 
# 3. calculate dc_i/dt for each GUV

# 4. calculate background intensity and convert this to c_0(t) via g quadruplex binding model

# 5. plot dc_/dt/A_GUV vs c_0-c_i (expect to see a positive linear relationship)


# as data includes actual G4 background for GUV permeability and later Gramicidin A experiments, start with these experiments


In [3]:
def set_plot_params(ax,xticks,yticks,
                    xlabel,ylabel,x_sciformat = 1,y_sciformat = 1):
    plt.tick_params(direction = 'in',top = True,right = True,left = True,bottom = True, length = 6)


    if x_sciformat != 1 or y_sciformat != 1:
        xticklabels = np.array(xticks)/x_sciformat
        yticklabels = np.array(yticks)/y_sciformat
        
    else:
        xticklabels = xticks
        yticklabels = yticks
        
    ax.set_xticks(xticks)
    ax.set_xticklabels(xticklabels,fontsize = 15)

    ax.set_yticks(yticks)
    ax.set_yticklabels(yticklabels,fontsize = 15)

    ax.set_xlabel(xlabel,fontsize = 18)
    ax.set_ylabel(ylabel,fontsize = 18)



In [4]:
App = 3.16 #um^2
Amin= 40*App*1e-12 #m^2
# G quadruplex model binding


def exp_I(c, k = 8.8,A = 0.39):
    return  A+ (1-A)/(k_1*c**2+1)

def inv(I, k = 8.8,A = 0.39):
    
    if I > 1:
        return 0
    
    elif I < A:
        return 1
        
    else:
        return np.sqrt((1/k)*((1-A)/(I-A)-1))


#smoothing configs

sigma = 101




# Calibration model fit


**If you have already fitted a calibration function and saved the parameters skip this section**


In [5]:
fitsdf = pd.read_csv('../Calibrations/Calibration_approx_fit_params.csv')

fit = fitsdf['Fitting Params']

def fit_func(I,fit):
    
    c = np.zeros_like(I)
    
    for i in range(1,len(fit)+1):

        c += fit[i-1]*(-np.log(I))**(len(fit)-i)
        print(len(fit)-i)
    return c

In [6]:

t0 = 50
t1 = 150
dt = 30/60

In [7]:
# load 260pM Gramicidin A experiment

dfI = pd.read_csv('../KineticsofLeakageGUV/collatedIabs.csv')
dfA = pd.read_csv('../KineticsofLeakageGUV/collatedAabs.csv')

In [8]:
dfI = dfI.iloc[:,1:]
dfA = dfA.iloc[:,1:]

In [9]:
dfA = dfA.fillna(0)
dfI = dfI.fillna(0)

# Remove small detected objects, most likely not GUVs

**check that the size is appropriate for the experiment**

In [10]:
# Remove small detected objects, most likely not GUVs
App = 3.16 #um^2
Amin= 75*App*1e-12 #m^2


for col in dfI.columns:
    
    if col in dfA.columns:
        area = 1e-12*App*np.mean(dfA[col].iloc[:30])
        
        if area < Amin:
            dfI.pop(col)
            dfA.pop(col)

# Remove intensity curves with sudden drops
 These are likely from GUVs suddenly escaping the trap

In [11]:

def remove_burst_events(data,threshold = 0.45):
    
    for column in data.columns:
        
        if len(data[column][data[column] < threshold]) >=1:
            data.pop(column)
            

In [12]:
# normalise intensities

for col in dfI.columns:
    dfI[col] = dfI[col]/np.mean(dfI[col][:10])
remove_burst_events(dfI)



%matplotlib qt
fig, ax = plt.subplots(1,1)

for col in dfI.columns:
    ax.plot(dfI[col].iloc[t0:])

# Smooth data

## Smoothing strategy

1. In experiments where there was relatively fast decay in intensity initially, but slows down (as exponential decays do..), yet there is still a lot of noise, it may be necessary to smooth different regions with different 'cutoff's.
When the intensity has dropped, the signal to noise drops. What's more during the slower period of intensity decay, there is increasing likelihood that some long timescale event will have happened to distort the data. This long timescale noise may be of a similar timescale to the 'signal' in the early period of rapid decay. 

2. The **solution** chosen here, is to have the user select a timepoint to bisect the time traces. The early period up until that timepoint is smoothed with the 1st user input smoothing parameter (usually between 11-21). Then the later period of slow decay is smoother with much larger smoothing settings (50-80). In order to ensure a smooth 'stitching' of these differently smoothed traces, we concatenate and repeat the smoothing with the smallest of the two specified smoothing parameters.

In [13]:
def smooth_decay(I,t0,t1=-1,smoothing_0 = 19,smoothing_1 = 81):
    
    
    if smoothing_0 > t1-t0 and t1 != -1:
        raise ValueError('Smoothing parameter cannot be greater than input data')
    
    smoothed_decay_0 = I.iloc[t0:t1]
    
    smoothed_decay_0 = savgol_filter(smoothed_decay_0,smoothing_0,1)
    
    if t1 != -1:
        
        smoothed_decay_1 = I.iloc[t1:]
        smoothed_decay_1  = savgol_filter(smoothed_decay_1,smoothing_1,1)
        
        smoothed_decay = np.concatenate((smoothed_decay_0,smoothed_decay_1))
    else:
        smoothed_decay = smoothed_decay_0
                               
    final_smoothed_decay = savgol_filter(smoothed_decay,smoothing_0,1)
    return final_smoothed_decay
                                  
                            

In [14]:
#Check smoothing still fits data
#
num = 8
fig,axs = plt.subplots(1,num)

for i,col in enumerate(dfI.columns[np.random.randint(0,len(dfI.columns),num)]):
    
    axs[i].plot(dfI[col])
    axs[i].plot(smooth_decay(dfI[col],t0,t1,smoothing_0 = 51,smoothing_1=151))
    

In [15]:
dfC_dict = {}

# can't exploit numpy broadcasting

for col in dfI.columns:
    
    smoothed_decay = smooth_decay(dfI[col],t0,t1,smoothing_0 = 51,smoothing_1=151)
#     print(smoothed_decay)
#     normalised_sd = smoothed_decay/np.mean(smoothed_decay[:30])
    
    cs = []
    for I in smoothed_decay:
#         print(I)
        cs.append(fit_func(I,fit))
    
    
    dfC_dict[col] = cs
    
dfC = pd.DataFrame(dfC_dict)

3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0


0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1


0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1


2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3


0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1


...

3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0


0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1


1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2


3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0


3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0


In [37]:
%matplotlib qt

fig, axs = plt.subplots(1,2)

t = dt*np.arange(0,len(dfC))
for col in dfC.columns:
    
    
    axs[0].plot(t,dfC[col])
    axs[1].plot(t,dfI[col].iloc[t0:])
    

    for ax in axs:
        ax.set_ylim([0,1])



In [38]:
len(dfC.keys())

176

In [16]:
# find representative background concentration variation

# tifs = glob('/media/marcus/9C33-6BBD/20210920_GramA_260pM07_3nM815_1mMKCl_1/260pM/*.tif')

# bgs = []

# fig, ax = plt.subplots(1,1)

# for tif in tifs:
    
#     vid = tf.TiffFile(tif)
    
#     frames = vid.asarray()
    
#     bg = np.median(frames,axis  =(1,2))
#     bg = np.array(bg)/np.max(bg)
#     bgs.append(bg)
    
    
#     ax.plot(bg)

# This confirms that the normalised background is the same for each chamber. Suggesting potassium concs are identical between chambers



In [21]:
# filter concentration data by gradient
# if 

fig, axs = plt.subplots(1,2)

for col in dfC.columns:
    
#     grad = np.gradient(gaussian(dfC[col],sigma = 5))
    
#     if len(grad[grad <= -0.0009])/len(grad) > 0.05:
#         dfC.pop(col)
#         continue
#     axs[0].hist(grad,15)
#     axs[1].plot(dfC[col])

NameError: name 'grad' is not defined

In [33]:
tifs = glob('/media/marcus/9C33-6BBD/20210427_OmpF_PCPG_KCL_Flush_2-20210427T184510Z-002/20210427_OmpF_PCPG_KCL_Flush_2/*.tif')
tif = tifs[-1]

vid = tf.TiffFile(tif)

frames = vid.asarray()
bg = np.median(frames,axis = (1,2))

bg = np.array(bg)-np.mean(bg[:30])
bg = bg/np.max(bg)



OME series: not an ome-tiff master file


In [73]:
bg

array([ 0.0416429 ,  0.06446092,  0.00741586, -0.02681118, -0.01540217,
       -0.00969766, -0.02110667, -0.01540217, -0.03251569,  0.00171135,
       -0.00969766,  0.00741586,  0.00171135, -0.01540217, -0.02681118,
       -0.02110667, -0.00399315,  0.01882487,  0.00171135,  0.00171135,
        0.01882487,  0.01312037, -0.00399315,  0.01312037,  0.03023388,
        0.01312037,  0.00171135, -0.01540217, -0.00399315, -0.01540217,
        0.00171135, -0.00399315, -0.02110667, -0.00969766,  0.00171135,
        0.00171135, -0.00399315, -0.00399315, -0.01540217, -0.01540217,
        0.00741586,  0.01312037,  0.00741586,  0.01312037,  0.01312037,
       -0.00969766, -0.00969766, -0.02110667,  0.00741586,  0.01312037,
       -0.03251569, -0.00399315, -0.00399315, -0.00969766, -0.01540217,
       -0.00969766, -0.00969766, -0.02110667,  0.03023388,  0.00741586,
        0.0416429 ,  0.00171135, -0.00399315,  0.01882487,  0.02452938,
        0.02452938,  0.03593839,  0.00741586,  0.00741586,  0.04

In [131]:
# c_bg = []
# for x in bg[360+t0:]:
#     c_bg.append(inv(x))

In [132]:
# fig, axs = plt.subplots(1,2)


# smoothed_background = gaussian(c_bg,sigma)
# axs[0].plot(smoothed_background)
# axs[1].plot(bg[360+t0:])

In [80]:
# drift in the background intensity over time, once the potassium has arrived, is causing a drifting predicted potassium concentration
# this is unlikely to be the case in reality.
# Therefore the best thing may be to just assume that after an initial 80 frame boundary region (20 mins) for this exp
# the potassium concentration externally reaches 1mM.


# Find concentration difference

In [76]:
# calculating c_ext - c_i

dfdeltaC_dict = {}

for col in dfC:
    
    dfdeltaC_dict[col] = 1-dfC[col]
    
dfdeltaC = pd.DataFrame(dfdeltaC_dict)

In [77]:
fig, axC = plt.subplots(1,1)

delete_cols = []

for col in dfdeltaC.columns:
    graddeltaC = np.gradient(dfdeltaC[col])
    
    
    if len(graddeltaC[graddeltaC > 0]) > 1:
        delete_cols.append(col)
        continue
        
    axC.plot(dfdeltaC[col])

In [78]:
for col in delete_cols:
    dfdeltaC.pop(col)

# Determine the flux

In [79]:
# now calculate J

# J = (1/A)*dN/dt = R/3* dc_i/dt

dfJ_dict = {}


for col in dfdeltaC:
    
    if col in dfA:
        print(col)
        delta_c = np.gradient(dfC[col],dt)/60 #molm^-3s^-1
        print(dfC[col])
        A = np.mean(dfA[col].iloc[:30])*App*1e-12 #m^2
#         if A < Amin:
#             continue
        R = np.sqrt(A/np.pi) #m
        
        dfJ_dict[col] = R/3*delta_c #molm^-2s^-1
        

dfJ = pd.DataFrame(dfJ_dict)



10062
0       -0.04522373244897007
1      -0.044579681612666955
2       -0.04393617557340054
3      -0.043293214234522794
4      -0.042650797498624354
5      -0.042008925267531055
6      -0.041367597442304116
7      -0.040726813923236516
8       -0.04008657460985135
9       -0.03944687940089975
10      -0.03880772819435873
11     -0.038169120887429575
12     -0.037531057376534165
13      -0.03689353755731514
14      -0.03625656132463234
15     -0.035620128572561006
16      -0.03498423919438969
17      -0.03434889308261853
18      -0.03371409012895556
19     -0.033079830224316875
20      -0.03244611325882301
21       -0.0318129391217971
22     -0.031180307701762777
23      -0.03054821888644201
24     -0.029916672562753297
25      -0.02928566861680765
26     -0.028754409225064496
27      -0.02819537145720344
28     -0.027629843175328152
29     -0.027074354190139007
               ...          
720      0.17229675635334618
721        0.172526598438305
722      0.17275632913270872
723     

In [80]:
fig, axs = plt.subplots(1,3)
legend = []

for col in dfJ.columns:

    legend.append(col)
#     print(dfdeltaC)

    axs[0].scatter(dfdeltaC[col],dfJ[col]*1e10, marker = '+', s = 10)
    print(dfJ[col])

    axs[1].plot(dt*np.arange(0,len(dfC[col])),dfC[col])

    
#     gradients = []
#     win = 10
#     for i in range(dfJ[col].shape[0]-(win-1)):
        
#         gradient = np.mean(np.gradient(dfJ[col].iloc[i:i+win]))
#         gradients.append(gradient)
        
    
    axs[2].plot(np.gradient(dfJ[col],dfdeltaC[col]))
axs[0].tick_params(direction = 'in',left = True,right = True,bottom = True,top = True,length = 6)
axs[1].tick_params(direction = 'in',left = True,right = True,bottom = True,top = True,length = 6)
axs[0].set_xlabel('[K_ext]-[K_int] [mM]',fontsize = 18)

axs[0].set_ylabel('J [molm^-2s^-1]',fontsize = 18)

axs[1].set_ylabel('[K_int] [mM]',fontsize = 18)


axs[1].set_xlabel(' T [mins]',fontsize = 18)


#xticks

axs[0].set_xticks([0,0.5,1])
axs[0].set_xticklabels([0,0.5,1],fontsize = 15)
axs[0].set_xlim([0,1.05])

axs[1].set_xticks([0,60,120])
axs[1].set_xticklabels([0,60,120],fontsize = 15)

#yticks

axs[0].set_yticks([0,0.01,0.02])
axs[0].set_yticklabels([0,0.01,0.02],fontsize = 15)

axs[0].set_ylim([-0.0005,0.0105])
axs[1].set_yticks([0, 0.5,1])
axs[1].set_yticklabels([0,0.5,1],fontsize = 15)


axs[0].set_ylim([-0.0005,0.0205])
axs[1].set_ylim([-0.05,1.05])


plt.legend(legend)
#xticks

# axs[0].set_xticks([0.5,0.75,1])
# axs[0].set_xticklabels([0.5,0.75,1],fontsize = 15)

# axs[1].set_xticks([0,20,40])
# axs[1].set_xticklabels([0,20,40],fontsize = 15)

# #yticks

# axs[0].set_yticks([0,0.005,0.01,0.015])
# axs[0].set_yticklabels([0,0.005,0.01,0.015],fontsize = 15)

# axs[0].set_ylim([-0.0005,0.0155])
# axs[1].set_yticks([0, 0.25,0.5])
# axs[1].set_yticklabels([0,0.25,0.5],fontsize = 15)


# plt.rcParams['text.usetex'] = True

# def myticks(x,pos):

#     if x == 0: return "$0$"

#     exponent = int(np.log10(x))
#     coeff = x/10**exponent

#     return r"${:2.0f} \times 10^{{ {:2d} }}$".format(coeff,exponent)

# axs[0].yaxis.set_major_formatter(ticker.FuncFormatter(myticks))

0      6.297840e-11
1      6.295176e-11
2      6.289849e-11
3      6.284523e-11
4      6.279199e-11
5      6.273875e-11
6      6.268552e-11
7      6.263230e-11
8      6.257909e-11
9      6.252589e-11
10     6.247270e-11
11     6.241952e-11
12     6.236635e-11
13     6.231319e-11
14     6.226004e-11
15     6.220690e-11
16     6.215377e-11
17     6.210065e-11
18     6.204754e-11
19     6.199445e-11
20     6.194136e-11
21     6.188829e-11
22     6.183522e-11
23     6.178217e-11
24     6.172913e-11
25     5.682586e-11
26     5.330726e-11
27     5.498275e-11
28     5.480924e-11
29     5.413407e-11
           ...     
720    2.248052e-11
721    2.246962e-11
722    2.245873e-11
723    2.244785e-11
724    2.243698e-11
725    2.242612e-11
726    2.241527e-11
727    2.240443e-11
728    2.239359e-11
729    2.238277e-11
730    2.237195e-11
731    2.236114e-11
732    2.235034e-11
733    2.233955e-11
734    2.232877e-11
735    2.231800e-11
736    2.230724e-11
737    2.229649e-11
738    2.228574e-11


0      2.848850e-10
1      2.844502e-10
2      2.835807e-10
3      2.827118e-10
4      2.818434e-10
5      2.809757e-10
6      2.801085e-10
7      2.792420e-10
8      2.783762e-10
9      2.775110e-10
10     2.766464e-10
11     2.757826e-10
12     2.749195e-10
13     2.740571e-10
14     2.731954e-10
15     2.723345e-10
16     2.714744e-10
17     2.706151e-10
18     2.697566e-10
19     2.688990e-10
20     2.680422e-10
21     2.671862e-10
22     2.663312e-10
23     2.654771e-10
24     2.646239e-10
25     2.702732e-10
26     2.765854e-10
27     2.775625e-10
28     2.779816e-10
29     2.761055e-10
           ...     
720    4.103693e-11
721    4.108492e-11
722    4.113316e-11
723    4.118164e-11
724    4.123037e-11
725    4.127935e-11
726    4.132858e-11
727    4.137805e-11
728    4.142778e-11
729    4.147775e-11
730    4.152798e-11
731    4.157845e-11
732    4.162918e-11
733    4.168016e-11
734    4.173139e-11
735    4.178288e-11
736    4.183462e-11
737    4.188661e-11
738    4.193886e-11


# Plot the Flux against concentration gradient



In [175]:
%matplotlib qt
figJ, axJ = plt.subplots(1,1)
figC, axC = plt.subplots(1,1)


P_threshold = 3.5e-10

def Jfit(deltac,k,c):
    return k*deltac + c

p0 = [1e-14,0]
Pparams = {}
cols = []

# print(dfJ.columns)
for i,col in enumerate(dfJ.columns):
    
    
    t = dt*np.arange(0,len(dfC[col]))
    
    J = dfJ[col]
    deltaC = dfdeltaC[col]
    
#     deltaC_bar = np.linspace(dfC[col].min(),1)
    
    params = curve_fit(Jfit,deltaC.iloc[deltaC.to_numpy().astype(float)<0.95],J.iloc[deltaC.to_numpy().astype(float)<0.95],p0)
    
# #     print(params)
    J_bar = Jfit(deltaC,*params[0])
    P = params[0][0]
    dP = np.sqrt(params[1][0][0])
    print(dP/P, P)
    
    if P < 0:
        dfJ.pop(col)
        dfdeltaC.pop(col)
        continue
        
#     if dP/P > 0.1 or P < 0:
#         dfJ.pop(col)
#         dfdeltaC.pop(col)        
#         continue
        
#     if len(J.iloc[(deltaC < 0.7).to_numpy()]) < 1:
#         continue
    
    Pparams[col] = params

    cols.append(col)
    
    print(col)
    
    
    # plot fluxes
    
    
    axJ.scatter(deltaC,J,alpha = 0.25)
#     axJ.plot(deltaC,J_bar)
    
    #plot the Intensity vs time
    
    axC.plot(t,dfI[col].iloc[t0:])
 
#Flux plot params


axJ.set_xticks([0.5,1])
axJ.set_xlim([0.45,1.05])
axJ.set_xticklabels([0.5,1],fontsize = 15)

axJ.set_xlabel('$[K]_{ext} - [K]_{in}$ [mM]',fontsize = 18)
axJ.set_yticks([0,5e-11,1e-10,1.5e-10,2e-10])
axJ.set_yticklabels([0,0.5,1,1.5,2],fontsize = 15)

axJ.set_ylim([-1e-11,5.1e-10])
#  
axJ.set_ylabel('J  [$10^{-10}$ mol$m^{-2}s^{-1}$]',fontsize = 18)
axJ.tick_params(direction = 'in',left = True,right = True, top = True, bottom = True,length = 7)

axC.set_xticks([0,20,40])
axC.set_xticklabels([0,20,40],fontsize = 15)
axC.set_xlabel('Time [mins]',fontsize = 18)

axC.set_yticks([0,0.5,1])
axC.set_yticklabels([0,0.5,1],fontsize = 15)
axC.set_ylabel('Rel I',fontsize = 18 )
axC.set_ylim([-0.05,1.05])
# axC.set_xlim([0,45])

# global params

axC.tick_params(direction = 'in',left = True,right = True, top = True, bottom = True,length = 7)


0.04168091834403046 3.583682049426246e-10
10062
0.02980856742969001 4.1775460073499097e-10
10070
0.01892807172861665 2.441376664143631e-10
10100
0.09423330247601862 1.0708764584088174e-10
10129
0.3614756144952937 2.6465274019764145e-11
10142
0.02558222090546062 1.5067029108623648e-10
07066
-0.05190513792017038 -1.9547735036704156e-10
0.05399629048300018 2.841689872467148e-10
07086
0.03370905009505522 1.6299888992337697e-10
07106
0.050206984406381445 9.720627644987636e-11
07114
0.020507598510960453 1.0323204217758652e-10
07148
0.07917125984797392 6.95111233368557e-11
06004
0.06614210663024432 1.1857558950120184e-10
06032
0.030373765533713234 1.479744194348916e-10
06053
0.1088897495863419 9.800505237233246e-11
06057
0.01819016653838795 4.2864398929038137e-10
06061
0.02523293125778248 2.950065000183048e-10
06062
0.024339515796404965 1.9208005269790144e-10
06065
-0.1674839844236854 -4.697682048150284e-11
0.02005810202054418 2.8080360902271687e-10
06132
0.0180403940906191 3.335641410081621e

# Save Permeability values

In [176]:
P_df = {'P ms^-1': [Pparams[key][0][0] for key in Pparams.keys()],
       'dP/P': [np.sqrt(Pparams[key][1][0][0])/Pparams[key][0][0] for key in Pparams.keys()],
       'A':[np.mean(dfA[key].iloc[:30]) for key in Pparams.keys()]}
        
P_identified = {key:[Pparams[key][0][0]] for key in Pparams.keys()}
P_identified = pd.DataFrame(P_identified)
P_df = pd.DataFrame(P_df)

In [177]:
P_df['P cms^-1'] = P_df['P ms^-1']*100

In [178]:
P_df

P ms^-1      dP/P           A      P cms^-1
0   3.583682e-10  0.041681   77.000000  3.583682e-08
1   4.177546e-10  0.029809   97.166667  4.177546e-08
2   2.441377e-10  0.018928   85.900000  2.441377e-08
3   1.070876e-10  0.094233  108.933333  1.070876e-08
4   2.646527e-11  0.361476  171.633333  2.646527e-09
5   1.506703e-10  0.025582  105.666667  1.506703e-08
6   2.841690e-10  0.053996  172.533333  2.841690e-08
7   1.629989e-10  0.033709  100.466667  1.629989e-08
8   9.720628e-11  0.050207  144.466667  9.720628e-09
9   1.032320e-10  0.020508   90.566667  1.032320e-08
10  6.951112e-11  0.079171   92.466667  6.951112e-09
11  1.185756e-10  0.066142  156.033333  1.185756e-08
12  1.479744e-10  0.030374  118.300000  1.479744e-08
13  9.800505e-11  0.108890  112.600000  9.800505e-09
14  4.286440e-10  0.018190   88.633333  4.286440e-08
15  2.950065e-10  0.025233   81.400000  2.950065e-08
16  1.920801e-10  0.024340  146.566667  1.920801e-08
17  2.808036e-10  0.020058  176.666667  2.808036e-08
18  3.335641e-10  0.018040  126.566667  3.335641e-08
19  5.328424e-11  0.179858   96.866667  5.328424e-09
20  1.602341e-11  0.605304  110.166667  1.602341e-09
21  1.664963e-10  0.040621  104.500000  1.664963e-08
22  2.932132e-10  0.052231  119.533333  2.932132e-08
23  7.385579e-11  0.140218   78.433333  7.385579e-09
24  1.369607e-10  0.070559   87.266667  1.369607e-08
25  2.208449e-10  0.058972   76.100000  2.208449e-08
26  5.418008e-10  0.010470   85.633333  5.418008e-08
27  1.170913e-10  0.038245   86.033333  1.170913e-08
28  6.088053e-11  0.178268   86.433333  6.088053e-09
29  1.733225e-10  0.034127   99.966667  1.733225e-08
30  6.855165e-11  0.152444  115.666667  6.855165e-09
31  8.206517e-11  0.243075  101.600000  8.206517e-09
32  1.566913e-10  0.055530  225.366667  1.566913e-08
33  5.803813e-11  0.113745  161.233333  5.803813e-09
34  1.154251e-10  0.032334  155.266667  1.154251e-08
35  3.692231e-12  4.832110  150.233333  3.692231e-10
36  3.100303e-10  0.027288  106.533333  3.100303e-08
37  1.645902e-10  0.044367  112.666667  1.645902e-08
38  2.089829e-10  0.046051  136.566667  2.089829e-08
39  2.196125e-10  0.048990  113.233333  2.196125e-08
40  2.305306e-10  0.043576   75.000000  2.305306e-08
41  5.516228e-10  0.021640  174.633333  5.516228e-08
42  1.148211e-10  0.080599  164.666667  1.148211e-08
43  4.472736e-11  0.299429  206.066667  4.472736e-09
44  5.114554e-10  0.016951  106.866667  5.114554e-08

In [86]:
fig,ax = plt.subplots(1,1)

ax.hist(np.log10(P_df['P cms^-1'].iloc[P_df['P ms^-1'].to_numpy() > 0].iloc[P_df['dP/P'].iloc[P_df['P ms^-1'].to_numpy() > 0].to_numpy() < 0.1]),6, alpha = 0.3, edgecolor = 'k')

xticks = [-8.5,-8,-7.5]
yticks = [0,5,10]
xlabel = 'Log(P $[ cms^{-1}] $)'
ylabel = '# GUVs'

set_plot_params(ax,xticks,yticks,
                    xlabel,ylabel,x_sciformat = 1,y_sciformat = 1)

ax.set_ylim([0,11])

(0, 11)

In [268]:
P_df.to_csv('Permeabilities_GUV.csv')

In [170]:
P_df

P ms^-1      dP/P           A      P cms^-1
0   5.114554e-10  0.016951   77.000000  5.114554e-08
1   5.114554e-10  0.016951   97.166667  5.114554e-08
2   5.114554e-10  0.016951   85.900000  5.114554e-08
3   5.114554e-10  0.016951  108.933333  5.114554e-08
4   5.114554e-10  0.016951  171.633333  5.114554e-08
5   5.114554e-10  0.016951  105.666667  5.114554e-08
6   5.114554e-10  0.016951   79.200000  5.114554e-08
7   5.114554e-10  0.016951  172.533333  5.114554e-08
8   5.114554e-10  0.016951  100.466667  5.114554e-08
9   5.114554e-10  0.016951  144.466667  5.114554e-08
10  5.114554e-10  0.016951   90.566667  5.114554e-08
11  5.114554e-10  0.016951   92.466667  5.114554e-08
12  5.114554e-10  0.016951  156.033333  5.114554e-08
13  5.114554e-10  0.016951  118.300000  5.114554e-08
14  5.114554e-10  0.016951  112.600000  5.114554e-08
15  5.114554e-10  0.016951   88.633333  5.114554e-08
16  5.114554e-10  0.016951   81.400000  5.114554e-08
17  5.114554e-10  0.016951  146.566667  5.114554e-08
18  5.114554e-10  0.016951  116.466667  5.114554e-08
19  5.114554e-10  0.016951  176.666667  5.114554e-08
20  5.114554e-10  0.016951  126.566667  5.114554e-08
21  5.114554e-10  0.016951   96.866667  5.114554e-08
22  5.114554e-10  0.016951  174.333333  5.114554e-08
23  5.114554e-10  0.016951  110.166667  5.114554e-08
24  5.114554e-10  0.016951  104.500000  5.114554e-08
25  5.114554e-10  0.016951  107.433333  5.114554e-08
26  5.114554e-10  0.016951  119.533333  5.114554e-08
27  5.114554e-10  0.016951   78.433333  5.114554e-08
28  5.114554e-10  0.016951   87.266667  5.114554e-08
29  5.114554e-10  0.016951   76.100000  5.114554e-08
30  5.114554e-10  0.016951   85.633333  5.114554e-08
31  5.114554e-10  0.016951   86.033333  5.114554e-08
32  5.114554e-10  0.016951   86.433333  5.114554e-08
33  5.114554e-10  0.016951   99.966667  5.114554e-08
34  5.114554e-10  0.016951  115.666667  5.114554e-08
35  5.114554e-10  0.016951   86.166667  5.114554e-08
36  5.114554e-10  0.016951  166.933333  5.114554e-08
37  5.114554e-10  0.016951  101.600000  5.114554e-08
38  5.114554e-10  0.016951  225.366667  5.114554e-08
39  5.114554e-10  0.016951  161.233333  5.114554e-08
40  5.114554e-10  0.016951  155.266667  5.114554e-08
41  5.114554e-10  0.016951  150.233333  5.114554e-08
42  5.114554e-10  0.016951  106.533333  5.114554e-08
43  5.114554e-10  0.016951  112.666667  5.114554e-08
44  5.114554e-10  0.016951  136.566667  5.114554e-08
45  5.114554e-10  0.016951  113.233333  5.114554e-08
46  5.114554e-10  0.016951   75.000000  5.114554e-08
47  5.114554e-10  0.016951  174.633333  5.114554e-08
48  5.114554e-10  0.016951  164.666667  5.114554e-08
49  5.114554e-10  0.016951  206.066667  5.114554e-08
50  5.114554e-10  0.016951  106.866667  5.114554e-08

In [70]:
# model membrane voltage using membrane capacitance

# Q = VC

# V = ze(cK - cCl)*Vol/C

# for a completely potassium selective membrane
# c = 1e-6 #F/cm^-2
c = 1e-2 #F/m^2

C = c*4*np.pi*(1.25e-5)**2

V = (96485*(1)*(4/3)*np.pi*(1.25e-5)**3)/C


# Save Flux vs deltaC data


In [269]:
dfJ.to_csv('Flux_GUV.csv')
dfdeltaC.to_csv('deltaC_GUV.csv')
P_identified.to_csv('PbyGUVId_GUV.csv')

# Compute average J vs deltaC to see if on average there is a membrane potential effect

In [239]:
deltaCbins = np.linspace(0.6,0.95,60)

deltaC_arr = dfdeltaC[cols].to_numpy()

dfJoverP = dfJ[cols]

for col in dfJoverP.columns:
    dfJoverP[col] = dfJoverP[col].to_numpy()/P_identified[col].iloc[0]
    
    
J_arr = dfJoverP.to_numpy()

J_mean = []
deltaC_mean = []

J_scatter = []

for i in range(len(deltaCbins)-1):
    
    deltaC_mean.append(np.median(deltaC_arr[(deltaC_arr < deltaCbins[i+1]) * (deltaC_arr >deltaCbins[i])]))
    J_mean.append(np.median(J_arr[(deltaC_arr < deltaCbins[i+1]) * (deltaC_arr >deltaCbins[i])]))
    J_scatter.append(np.std(J_arr[(deltaC_arr < deltaCbins[i+1]) * (deltaC_arr >deltaCbins[i])])/np.sqrt(len(J_arr[(deltaC_arr < deltaCbins[i+1]) * (deltaC_arr >deltaCbins[i])])))
    print(len(J_arr[(deltaC_arr < deltaCbins[i+1]) * (deltaC_arr >deltaCbins[i])]))
J_mean = P_identified.iloc[0,:].mean()*np.array(J_mean)
J_scatter = P_identified.iloc[0,:].mean()*np.array(J_scatter)

136
148
150
171
206
193
190
166
145
130
116
135
151
143
140
138
136
171
165
160
181
208
231
227
196
195
216
224
268
410
486
538
574
625
708
654
632
684
752
859
877
885
939
1028
1064
887
839
777
766
793
783
737
698
691
659
605
621
610
614


In [279]:
figm,axm = plt.subplots(1,1)

upper_bound = np.array(J_mean) + np.array(J_scatter)
lower_bound = np.array(J_mean) - np.array(J_scatter)
axm.scatter(deltaC_mean,J_mean,color = 'C0', marker = 'x',s = 15)
# axm.fill_between(deltaC_mean,lower_bound,upper_bound, alpha = 0.25,color = 'g')
l = axm.errorbar(deltaC_mean,J_mean,J_scatter,color = 'g')
l[0].remove()
axm.set_ylim([-1e-11,10e-11])

(-1e-11, 1e-10)

In [240]:
help(ax.errorbar)

Help on method errorbar in module matplotlib.axes._axes:

errorbar(x, y, yerr=None, xerr=None, fmt='', ecolor=None, elinewidth=None, capsize=None, barsabove=False, lolims=False, uplims=False, xlolims=False, xuplims=False, errorevery=1, capthick=None, *, data=None, **kwargs) method of matplotlib.axes._subplots.AxesSubplot instance
    Plot y versus x as lines and/or markers with attached errorbars.
    
    *x*, *y* define the data locations, *xerr*, *yerr* define the errorbar
    sizes. By default, this draws the data markers/lines as well the
    errorbars. Use fmt='none' to draw errorbars without any data markers.
    
    Parameters
    ----------
    x, y : scalar or array-like
        The data positions.
    
    xerr, yerr : scalar or array-like, shape(N,) or shape(2,N), optional
        The errorbar sizes:
    
        - scalar: Symmetric +/- values for all data points.
        - shape(N,): Symmetric +/-values for each data point.
        - shape(2,N): Separate - and + values fo

In [143]:

def JvsCLinear(dC,P,c):
    return P*dC + c

params = curve_fit(JvsCLinear,deltaC_mean,J_mean,p0 = [1,-0.2])

In [271]:
axm.set_ylim([-1e-11,11e-11])
axm.set_xlim([0.55,1])


(0.55, 1)

In [145]:
dC_bar = np.linspace(0.6,1,100)
J_pred = JvsCLinear(dC_bar,*params[0])
axm.plot(dC_bar,J_pred)

In [281]:
# make plot look nice
xticks = [0.6,0.8,1]
yticks = [0,5e-11,1e-10]
set_plot_params(axm,xticks,yticks,'$ \Delta C  [mM] $','J $ 10^{11} [molm^{-2}s^{-1}]$',y_sciformat=1e-11)
axm.set_yticklabels([0,5,10],fontsize = 20)
axm.set_ylim([-1e-11,11e-11])
axm.set_xlim([0.55,1])
axm.set_xticklabels(xticks,fontsize = 20),
axm.set_xlabel('$ \Delta C  [mM] $',fontsize = 22)
axm.set_ylabel('J $ 10^{11} [molm^{-2}s^{-1}]$',fontsize = 22)

Text(43.08333333333333, 0.5, 'J $ 10^{11} [molm^{-2}s^{-1}]$')

# Load OmpF mean Flux data for plotting

In [263]:
dfFlux = pd.read_csv('20210420_OmpF_MeanFluxvsdeltaC.csv')
J_OmpF = dfFlux['J']
deltaC_OmpF = dfFlux['deltaC']
semJ_OmpF = dfFlux['semJ']

In [277]:
figm,axm = plt.subplots(1,1)

# upper_bound = np.array(J_mean) + np.array(J_scatter)
# lower_bound = np.array(J_mean) - np.array(J_scatter)
# axm.scatter(deltaC_mean,J_mean, marker = 'x',s = 15)
# l = axm.errorbar(deltaC_mean,J_mean,J_scatter,color = 'g')
# l[0].remove()
# axm.fill_between(deltaC_mean,lower_bound,upper_bound, alpha = 0.25,color = 'g')
# axm.set_ylim([-1e-11,10e-11])
axm.scatter(deltaC_OmpF,J_OmpF, c= 'C1', marker = 'x',s = 15)
axm.set_ylim([-1e-9,11e-9])
# axm.fill_between(deltaC_OmpF,J_lower_OmpF,J_upper_OmpF, alpha = 0.25,color = 'C1')
l = axm.errorbar(deltaC_OmpF,J_OmpF,semJ_OmpF,color = 'C1', alpha = 0.5)
l[0].remove()


In [278]:
# make plot look nice
xticks = [0.4,0.6,0.8,1]
yticks = [0,5e-9,10e-9]

set_plot_params(axm,xticks,yticks,'$ \Delta C  [mM] $','J $ 10^{9} [molm^{-2}s^{-1}]$',y_sciformat=1e-9)